In [1]:
import pc_rasterize as pcr
import glob
import numpy as np

In [2]:
print(pcr.get_file_quickinfo("../data/als_data/USGS_LPC_CA_SierraNevada_B22_10SGJ2967.laz"))

LidarInfo(n_points=35921728, dims=('X', 'Y', 'Z', 'Intensity', 'ReturnNumber', 'NumberOfReturns', 'ScanDirectionFlag', 'EdgeOfFlightLine', 'Classification', 'Synthetic', 'KeyPoint', 'Withheld', 'Overlap', 'ScanAngleRank', 'UserData', 'PointSourceId', 'GpsTime', 'ScanChannel'), crs=CRS.from_wkt('COMPD_CS["NAD83(2011) / UTM zone 10N + NAVD88 height - Geoid18 (m)",PROJCS["NAD83(2011) / UTM zone 10N",GEOGCS["NAD83(2011)",DATUM["NAD83_National_Spatial_Reference_System_2011",SPHEROID["GRS 1980",6378137,298.257222101]],PRIMEM["Greenwich",0,AUTHORITY["EPSG","8901"]],UNIT["degree",0.0174532925199433,AUTHORITY["EPSG","9122"]],AUTHORITY["EPSG","6318"]],PROJECTION["Transverse_Mercator"],PARAMETER["latitude_of_origin",0],PARAMETER["central_meridian",-123],PARAMETER["scale_factor",0.9996],PARAMETER["false_easting",500000],PARAMETER["false_northing",0],UNIT["meter",1],AXIS["X",EAST],AXIS["Y",NORTH],AUTHORITY["EPSG","6339"]],VERT_CS["NAVD88 height - Geoid18 (m)",VERT_DATUM["North American Vertical Dat

In [3]:
# files = sorted(glob.glob("../data/als_data/USGS_LPC_CA_SierraNevada_B22_10SGJ2967.laz"))
files = sorted(glob.glob("../data/als_data/*.laz"))
# Create a GeoBox grid specification with a 100m buffer around data
geobox = pcr.build_geobox(files, resolution=1., crs="5070")
# Build a lazy CHM raster
chm = pcr.rasterize(
    files,
    geobox,
    cell_func="max",
    # Set custom dask chunk-size
    chunksize=(1000, 1000),
    nodata=np.nan,
    pdal_filters=[
    {
        "type":"filters.range",
        "limits":"Classification[1:5]"
    },
    {
      "type":"filters.outlier"
    },
    {
        "type":"filters.hag_nn"
    },
    {
        "type":"filters.ferry",
        "dimensions":"HeightAboveGround=>Z"
    },
    {
      "type":"filters.outlier"
    },
    {
        "type": "filters.expression",
        "expression": "Z < 75"
    }
    ]
)

In [4]:
from dask.distributed import Client, LocalCluster, Lock

with LocalCluster(n_workers=8, threads_per_worker=4, memory_limit='24GB') as cluster, Client(cluster) as client:
    chm.rio.to_raster("../data/chm.tiff", tiled=True, lock=Lock("rio"))